In [1]:
!pip install pytesseract evaluate transformers datasets rouge-score nltk tensorboard py7zr --upgrade

In [2]:
!sudo apt-get install git-lfs --yes

Reading package lists... Done
Building dependency tree       
Reading state information... Done
git-lfs is already the newest version (2.9.2-1).
0 upgraded, 0 newly installed, 0 to remove and 15 not upgraded.


In [3]:
from huggingface_hub import notebook_login

notebook_login()

In [4]:
dataset_id = "samsum"

In [5]:
from datasets import load_dataset

# Load dataset from the hub
dataset = load_dataset(dataset_id)

print(f"Train dataset size: {len(dataset['train'])}")
print(f"Test dataset size: {len(dataset['test'])}")

# Train dataset size: 14732
# Test dataset size: 819

  0%|          | 0/3 [00:00<?, ?it/s]

Train dataset size: 14732
Test dataset size: 819


In [6]:
from random import randrange


sample = dataset['train'][randrange(len(dataset["train"]))]
print(f"dialogue: \n{sample['dialogue']}\n---------------")
print(f"summary: \n{sample['summary']}\n---------------")

dialogue: 
Sarah: Annie, you know you are using up your Internet allowance much quicker this month?
Annie: How much have I got left, Mum?
Sarah: just 2GB for the next 12 days.
Annie: That's no good. Can't think how that happened.
---------------
summary: 
Sarah informed Annie that she is using her internet allowance quicker this month. Annie has 2GB left for the next 12 days.
---------------


In [7]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

model_id="google/flan-t5-base"

# Load tokenizer of FLAN-t5-base
tokenizer = AutoTokenizer.from_pretrained(model_id)

In [8]:
from datasets import concatenate_datasets

# The maximum total input sequence length after tokenization.
# Sequences longer than this will be truncated, sequences shorter will be padded.
tokenized_inputs = concatenate_datasets([dataset["train"], dataset["test"]]).map(lambda x: tokenizer(x["dialogue"], truncation=True), batched=True, remove_columns=["dialogue", "summary"])
max_source_length = max([len(x) for x in tokenized_inputs["input_ids"]])
print(f"Max source length: {max_source_length}")

# The maximum total sequence length for target text after tokenization.
# Sequences longer than this will be truncated, sequences shorter will be padded."
tokenized_targets = concatenate_datasets([dataset["train"], dataset["test"]]).map(lambda x: tokenizer(x["summary"], truncation=True), batched=True, remove_columns=["dialogue", "summary"])
max_target_length = max([len(x) for x in tokenized_targets["input_ids"]])
print(f"Max target length: {max_target_length}")

Max source length: 512


Map:   0%|          | 0/15551 [00:00<?, ? examples/s]

Max target length: 95


In [9]:
def preprocess_function(sample,padding="max_length"):
    # add prefix to the input for t5
    inputs = ["summarize: " + item for item in sample["dialogue"]]

    # tokenize inputs
    model_inputs = tokenizer(inputs, max_length=max_source_length, padding=padding, truncation=True)

    # Tokenize targets with the `text_target` keyword argument
    labels = tokenizer(text_target=sample["summary"], max_length=max_target_length, padding=padding, truncation=True)

    # If we are padding here, replace all tokenizer.pad_token_id in the labels by -100 when we want to ignore
    # padding in the loss.
    if padding == "max_length":
        labels["input_ids"] = [
            [(l if l != tokenizer.pad_token_id else -100) for l in label] for label in labels["input_ids"]
        ]

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_dataset = dataset.map(preprocess_function, batched=True, remove_columns=["dialogue", "summary", "id"])
print(f"Keys of tokenized dataset: {list(tokenized_dataset['train'].features)}")

Map:   0%|          | 0/819 [00:00<?, ? examples/s]

Keys of tokenized dataset: ['input_ids', 'attention_mask', 'labels']


In [10]:
from transformers import AutoModelForSeq2SeqLM

# huggingface hub model id
model_id="google/flan-t5-base"

# load model from the hub
model = AutoModelForSeq2SeqLM.from_pretrained(model_id)

In [11]:
import evaluate
import nltk
import numpy as np
from nltk.tokenize import sent_tokenize
nltk.download("punkt")

# Metric
metric = evaluate.load("rouge")

# helper function to postprocess text
def postprocess_text(preds, labels):
    preds = [pred.strip() for pred in preds]
    labels = [label.strip() for label in labels]

    # rougeLSum expects newline after each sentence
    preds = ["\n".join(sent_tokenize(pred)) for pred in preds]
    labels = ["\n".join(sent_tokenize(label)) for label in labels]

    return preds, labels

def compute_metrics(eval_preds):
    preds, labels = eval_preds
    if isinstance(preds, tuple):
        preds = preds[0]
    decoded_preds = tokenizer.batch_decode(preds, skip_special_tokens=True)
    # Replace -100 in the labels as we can't decode them.
    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    # Some simple post-processing
    decoded_preds, decoded_labels = postprocess_text(decoded_preds, decoded_labels)

    result = metric.compute(predictions=decoded_preds, references=decoded_labels, use_stemmer=True)
    result = {k: round(v * 100, 4) for k, v in result.items()}
    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in preds]
    result["gen_len"] = np.mean(prediction_lens)
    return result

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [12]:
from transformers import DataCollatorForSeq2Seq

# we want to ignore tokenizer pad token in the loss
label_pad_token_id = -100
# Data collator
data_collator = DataCollatorForSeq2Seq(
    tokenizer,
    model=model,
    label_pad_token_id=label_pad_token_id,
    pad_to_multiple_of=8
)

In [13]:
pip install transformers[torch]

In [14]:
from huggingface_hub import HfFolder
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments

# Hugging Face repository id
repository_id = f"{model_id.split('/')[1]}-{dataset_id}"

# Define training args
training_args = Seq2SeqTrainingArguments(
    output_dir=repository_id,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    fp16=False, # Overflows with fp16
    learning_rate=5e-5,
    num_train_epochs=5,
    # logging & evaluation strategies
    logging_dir=f"{repository_id}/logs",
    logging_strategy="steps",
    logging_steps=500,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    save_total_limit=2,
    load_best_model_at_end=True,
    # metric_for_best_model="overall_f1",
    # push to hub parameters
    report_to="tensorboard",
    push_to_hub=False,
    hub_strategy="every_save",
    hub_model_id=repository_id,
    hub_token=HfFolder.get_token(),
)

# Create Trainer instance
trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=tokenized_dataset["train"],
    eval_dataset=tokenized_dataset["test"],
    compute_metrics=compute_metrics,
)

In [15]:
# Start training
trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
You're using a T5TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=9210, training_loss=1.3033124296206993, metrics={'train_runtime': 3255.6159, 'train_samples_per_second': 22.626, 'train_steps_per_second': 2.829, 'total_flos': 5.043922658131968e+16, 'train_loss': 1.3033124296206993, 'epoch': 5.0})

In [16]:
trainer.evaluate()

{'eval_loss': 1.3707613945007324,
 'eval_rouge1': 47.476,
 'eval_rouge2': 23.8125,
 'eval_rougeL': 40.0792,
 'eval_rougeLsum': 43.5826,
 'eval_gen_len': 17.134310134310134,
 'eval_runtime': 56.0421,
 'eval_samples_per_second': 14.614,
 'eval_steps_per_second': 1.838,
 'epoch': 5.0}

In [20]:
from huggingface_hub import notebook_login

notebook_login()

In [21]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [ ]:
trainer.push_to_hub("JeffGuo/my_model")

In [30]:
# Save our tokenizer and create model card
tokenizer.save_pretrained(repository_id)
trainer.create_model_card()
# Push the results to the hub
trainer.push_to_hub()

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ /usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_errors.py:261 in                  │
│ hf_raise_for_status                                                                              │
│                                                                                                  │
│   258 │   </Tip>                                                                                 │
│   259 │   """                                                                                    │
│   260 │   try:                                                                                   │
│ ❱ 261 │   │   response.raise_for_status()                                                        │
│   262 │   except HTTPError as e:                                                                 │
│   263 │   │   error_code = response.headers.get("X-Error-Code")                                  │
│   264                                                                                            │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/requests/models.py:960 in raise_for_status               │
│                                                                                                  │
│   957 │   │   │   http_error_msg = u'%s Server Error: %s for url: %s' % (self.status_code, rea   │
│   958 │   │                                                                                      │
│   959 │   │   if http_error_msg:                                                                 │
│ ❱ 960 │   │   │   raise HTTPError(http_error_msg, response=self)                                 │
│   961 │                                                                                          │
│   962 │   def close(self):                                                                       │
│   963 │   │   """Releases the connection back to the pool. Once this method has been             │
╰──────────────────────────────────────────────────────────────────────────────────────────────────╯
HTTPError: 403 Client Error: Forbidden for url: https://huggingface.co/api/repos/create

The above exception was the direct cause of the following exception:

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ /usr/local/lib/python3.10/dist-packages/huggingface_hub/hf_api.py:2308 in create_repo            │
│                                                                                                  │
│   2305 │   │   r = get_session().post(path, headers=headers, json=json)                          │
│   2306 │   │                                                                                     │
│   2307 │   │   try:                                                                              │
│ ❱ 2308 │   │   │   hf_raise_for_status(r)                                                        │
│   2309 │   │   except HTTPError as err:                                                          │
│   2310 │   │   │   if exist_ok and err.response.status_code == 409:                              │
│   2311 │   │   │   │   # Repo already exists and `exist_ok=True`                                 │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_errors.py:303 in                  │
│ hf_raise_for_status                                                                              │
│                                                                                                  │
│   300 │   │                                                                                      │
│   301 │   │   # Convert `HTTPError` into a `HfHubHTTPError` to display request information       │
│  

In [29]:
from transformers import pipeline
from random import randrange

# load model and tokenizer from huggingface hub with pipeline
summarizer = pipeline("summarization", model="/content/flan-t5-base-samsum/checkpoint-5526", device=0)
#summarizer = pipeline("summarization", model="/content/flan-t5-base-samsum/checkpoint-5526/content/t5-small-finetuned-xsum/checkpoint-12500", device=0)

# select a random test sample
sample = dataset['test'][randrange(len(dataset["test"]))]
print(f"dialogue: \n{sample['dialogue']}\n---------------")

# summarize dialogue
res = summarizer(sample["dialogue"])

print(f"flan-t5-base summary:\n{res[0]['summary_text']}")

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <cell line: 5>:5                                                                              │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/pipelines/__init__.py:885 in pipeline       │
│                                                                                                  │
│   882 │   │   │   │   tokenizer_kwargs = model_kwargs.copy()                                     │
│   883 │   │   │   │   tokenizer_kwargs.pop("torch_dtype", None)                                  │
│   884 │   │   │                                                                                  │
│ ❱ 885 │   │   │   tokenizer = AutoTokenizer.from_pretrained(                                     │
│   886 │   │   │   │   tokenizer_identifier, use_fast=use_fast, _from_pipeline=task, **hub_kwar   │
│   887 │   │   │   )                                                                              │
│   888                                                                                            │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/models/auto/tokenization_auto.py:709 in     │
│ from_pretrained                                                                                  │
│                                                                                                  │
│   706 │   │   if model_type is not None:                                                         │
│   707 │   │   │   tokenizer_class_py, tokenizer_class_fast = TOKENIZER_MAPPING[type(config)]     │
│   708 │   │   │   if tokenizer_class_fast and (use_fast or tokenizer_class_py is None):          │
│ ❱ 709 │   │   │   │   return tokenizer_class_fast.from_pretrained(pretrained_model_name_or_pat   │
│   710 │   │   │   else:                                                                          │
│   711 │   │   │   │   if tokenizer_class_py is not None:                                         │
│   712 │   │   │   │   │   return tokenizer_class_py.from_pretrained(pretrained_model_name_or_p   │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1809 in          │
│ from_pretrained                                                                                  │
│                                                                                                  │
│   1806 │   │   │   )                                                                             │
│   1807 │   │                                                                                     │
│   1808 │   │   if all(full_file_name is None for full_file_name in resolved_vocab_files.values(  │
│ ❱ 1809 │   │   │   raise EnvironmentError(                                                       │
│   1810 │   │   │   │   f"Can't load tokenizer for '{pretrained_model_name_or_path}'. If you wer  │
│   1811 │   │   │   │   "'https://huggingface.co/models', make sure you don't have a local direc  │
│   1812 │   │   │   │   f"Otherwise, make sure '{pretrained_model_name_or_path}' is the correct   │
╰──────────────────────────────────────────────────────────────────────────────────────────────────╯
OSError: Can't load tokenizer for '/content/flan-t5-base-samsum/checkpoint-5526'. If you were trying to load it 
from 'https://huggingface.co/models', make sure you don't have a local directory with the same name. Otherwise, 
make sure '/content/flan-t5-base-samsum/checkpoint-5526' is the correct path to a directory containing all relevant
files for a T5TokenizerFast tokenizer.